<a href="https://colab.research.google.com/github/alinaalborova/russian_idioms_processing/blob/main/IdiomSim_fastText.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Idiom Paraphrase Experiments


Based on [Idiom Paraphrases: Seventh Heaven vs Cloud Nine](https://www.aclweb.org/anthology/W15-2709v2.pdf) by Maria Pershina Yifan He Ralph Grishman.


## Import Libraries

In [ ]:
import numpy as np
import pandas as pd
from tqdm import tqdm_notebook
import warnings
warnings.filterwarnings('ignore')
import tensorflow as tf

In [ ]:
!pip install annoy
from tqdm import tqdm_notebook
import networkx as nx       
from annoy import AnnoyIndex

     |████████████████████████████████| 655kB 4.3MB/s 
  Created wheel for annoy: filename=annoy-1.17.0-cp37-cp37m-linux_x86_64.whl size=391626 sha256=34927751d561bbc880cfb16d905cf8e2a0a0952fc5df89b7e7d4580ba0fa8977
  Stored in directory: /root/.cache/pip/wheels/3a/c5/59/cce7e67b52c8e987389e53f917b6bb2a9d904a03246fadcb1e
Successfully built annoy


## Load Dataset

In [ ]:
from google.colab import drive
drive.mount("/content/drive")

Mounted at /content/drive


In [ ]:
dataset_dir = '/content/drive/MyDrive/IdiomSim/idiomSim_fastText.csv'
data = pd.read_csv(dataset_dir )
data.head()

Unnamed: 0  ...                                         Embeddings
0           1  ...  [array([ 0.00798603, -0.02980846, -0.00795335,...
1           2  ...  [array([ 0.00796384, -0.01759238,  0.08423605,...
2           3  ...  [array([-1.83622036e-02, -5.43518960e-02,  4.0...
3           4  ...  [array([ 1.20287456e-01,  4.73265536e-02, -8.5...
4           5  ...  [array([ 1.20287456e-01,  4.73265536e-02, -8.5...

[5 rows x 4 columns]

In [ ]:
data.drop('Unnamed: 0', axis=1, inplace=True)
data

Idiom  ...                                         Embeddings
0         и вот на тебе!  ...  [array([ 0.00798603, -0.02980846, -0.00795335,...
1      а был ли мальчик?  ...  [array([ 0.00796384, -0.01759238,  0.08423605,...
2                  а вот  ...  [array([-1.83622036e-02, -5.43518960e-02,  4.0...
3            а вот и нет  ...  [array([ 1.20287456e-01,  4.73265536e-02, -8.5...
4              вот и нет  ...  [array([ 1.20287456e-01,  4.73265536e-02, -8.5...
...                  ...  ...                                                ...
13935        ямская изба  ...  [array([-2.31777839e-02,  2.41265073e-02, -8.1...
13936       ясная голова  ...  [array([-1.50045734e-02,  4.23253551e-02, -7.0...
13937       яснее ясного  ...  [array([-1.54766778e-03, -1.74670722e-02,  1.4...
13938         ясное дело  ...  [array([ 3.33544910e-02, -2.12118160e-02, -1.8...
13939          ясны горы  ...  [array([-1.07486947e-02,  8.38018954e-04,  5.6...

[13940 rows x 3 columns]

In [ ]:
data.dropna(inplace=True)
data.shape

(13940, 3)

In [ ]:
from ast import literal_eval

[1.23, 2.34]

In [ ]:
tokens = data['Embeddings'].values

In [ ]:
full_tokens = []
for e in tokens:
  full_tokens.append

## Similarity Tricks

#### _Auxiliary_. Build TF-IDF

In [ ]:
tk = tf.keras.preprocessing.text.Tokenizer()
tk.fit_on_texts(data['Definition'])

tk_output = tk.sequences_to_matrix(tk.texts_to_sequences(data['Definition']), mode='tfidf')

In [ ]:
print(len(data['Definition']))
len(tk_output) == len(data['Definition'])

13940


True

In [ ]:
len(tk_output[0]) ## vocab size

20606

In [ ]:
MAX_LEN = len(max(full_tokens, key=len))
def align_tfidf(tk_output):
  weights_all = []
  for doc in tqdm_notebook(tk_output):
    weights = [float(0), ] # reserved for cls
    for w in doc:
      if w != float(0):
        weights.append(w)
    while len(weights) < MAX_LEN:
      weights.append(float(0))
    weights_all.append(weights)
  return weights_all

In [ ]:
tfidf_values = align_tfidf(tk_output)
len(tfidf_values)

## Build Annoy Index

In [ ]:
def build_index(embeddings):
  f = 300
  Index = AnnoyIndex(f, 'angular')  # Length of item vector to be indexed

  for index, vector in enumerate(embeddings):
    Index.add_item(index, vector)
  Index.build(100)

  return Index

### Lexical Similarity

Compute cosine similarity between vectors Vd1 and Vd2, representing idiom descriptions d1 and d2 and weight each word in these vectors by its tf-idf score:  
$lexSim(d1, d2) = cosine(\vec{v}_{d1}, \vec{v}_{d2})$

where $\vec{v}$ d is a $\left |V \right |$-dimensional vector with $V$
being the vocabulary of all definition words.

In [ ]:
print(len(full_tokens[1]))
print(len(full_tokens[2]))
len(tfidf_values[0])

6
24


96

1. Get Vd1 and Vd2, representing idiom descriptions d1 and d2 and weight each word in these vectors by its tf-idf score

In [ ]:
def get_all_vd_values(tokens, tfidf_values):
  """
  Multplies each token vector in an idiom by its tf-idf value.
  """
  vd_values_total = []
  for id, full_token in enumerate(list(tokens)): # for each sentence's tokens
    vd_values = []
    for i, el in enumerate(full_token):
      token_emb_by_tfidf = tf.math.multiply(el, tfidf_values[id][i])
      vd_values.append(token_emb_by_tfidf)
    vd_values_total.append(tf.math.reduce_mean(vd_values, axis=0))
  return vd_values_total

vd_values_all = get_all_vd_values(full_tokens, tfidf_values)
len(vd_values_all)

In [ ]:
def get_vd_values(idiom_id):
  '''
  idiom_tokens: list of strings
  '''
  #print('ID', idiom_id, list(data.Idiom)[idiom_id])
  try:
    idiom_tokens = list(full_tokens)[idiom_id]
  except:
    print('Error', idiom_id)
  idiom_tfidf_values = tfidf_values[idiom_id]
  vd_values = []
  for i, el in enumerate(idiom_tokens):
    token_emb_by_tfidf = tf.math.multiply(el, idiom_tfidf_values[i])
    vd_values.append(token_emb_by_tfidf)  
  return tf.math.reduce_mean(vd_values, axis=0)

In [ ]:
id_vd = build_index(vd_values_all)

In [ ]:
def calculate_lex_sim(i1_id, i2_id):
  return 1 / (1 + id_vd.get_distance(i1_id, i2_id))

### Semantical Similarity

To capture the overall meaning of the definitions d we combine word embeddings
for all words in d using two combination schemes:
* Averaged sum:  
$\vec{averaged}_{d} = \frac{1}{\left |d  \right |}\sum_{word \in d} \vec{emb}(word)$
* Weighted sum:   
$\vec{weighted}_{d} = \frac{1}{\sum_{word \in d}tfidf_{word}}\sum_{word \in d}tfidf_{word} \cdot  \vec{emb}(word)$   
<br><br>

Then semantic similarity is measured as $semSim(d1,d2)= cosine(comb_{d1}, comb_{d2})$,  
where
$\vec{comb}_{d}$ is a 100-dimensional vector combined from word embeddings
$\vec{emb}(word)$ or words in description $d$ using either averaged or weighted combination
schemes. 


#### Averaged Sum

$\vec{averaged}_{d} = \frac{1}{\left |d  \right |}\sum_{word \in d} \vec{emb}(word)$

get average of all words in d

In [ ]:
avg_sums = []
## Since we have normalized sentence vecs (all lenghts are 60), we won't additionaly divide by sent lenght.
for definition in full_tokens:
  avg_sums.append(tf.math.reduce_sum(definition, axis=0))
print(len(avg_sums))
avg_sums[:5][:10]

13940


[<tf.Tensor: shape=(300,), dtype=float32, numpy=
 array([ 2.66208593e-02, -5.65134645e-01, -2.43666857e-01, -1.74609244e-01,
        -1.47742152e-01, -1.52869597e-01, -3.37520212e-01,  4.74706218e-02,
         1.24948665e-01, -3.68642330e-01, -7.69634545e-02,  5.55755973e-01,
         1.75785899e-01,  3.37870985e-01,  3.83849442e-01,  1.00098640e-01,
        -8.64840969e-02,  2.63306558e-01, -6.05683684e-01, -3.80573899e-01,
        -5.79463243e-02,  4.42664146e-01, -1.95655957e-01, -7.05967695e-02,
         3.42415065e-01,  9.25168395e-02, -1.59238666e-01, -1.24054439e-02,
         1.65275671e-03,  1.95695162e-01,  1.94891363e-01,  1.16111465e-01,
        -1.26302883e-01,  1.34844214e-01, -2.61176527e-01,  5.24424434e-01,
         4.34548736e-01, -2.62865686e+00, -1.96853459e-01, -6.48796201e-01,
        -3.17133814e-01,  2.22262084e-01, -2.24094421e-01,  1.27141744e-01,
        -3.29574794e-02, -9.63630751e-02,  2.62385011e-01,  7.47582391e-02,
        -6.63882017e-01, -7.57411242e-0

### Build Annoy Index

In [ ]:
id_avg = build_index(avg_sums)

In [ ]:
len(avg_sums)

13940

In [ ]:
len(full_tokens[1])

6

In [ ]:

len(list(full_tokens)[1])

24

In [ ]:
def get_avg_sum(definition_tokens):
  return tf.math.reduce_sum(definition_tokens, axis=0)

#### semSim

Semantic similarity is measured as $semSim(d1,d2)= cosine(comb_{d1}, comb_{d2})$,  
where
$\vec{comb}_{d}$ is a 100-dimensional vector combined from word embeddings
$\vec{emb}(word)$ or words in description $d$ using either averaged or weighted combination
schemes. 

In [ ]:
def calculate_sem_sim_avg(i1_id, i2_id):
  return 1 / (1 + id_avg.get_distance(i1_id, i2_id))

In [ ]:
calculate_sem_sim_avg(list(data.Idiom).index('больное место'), list(data.Idiom).index('ахиллесова пята'))

0.4795502204410559

In [ ]:
calculate_sem_sim_avg(list(data.Idiom).index('брать в ежовые рукавицы'), list(data.Idiom).index('адамова голова'))

0.5019092919753674

In [ ]:
calculate_sem_sim_avg(list(data.Idiom).index('багрити руки в крови'), list(data.Idiom).index('белый негр'))

0.46053678512514706

### IdiomSim

* lexSim captures the actual lexical overlap
* semSim can better capture the closeness in semantic meaning

To find an optimal balance between the two we consider their weighted sum:  
$IdiomSim(d1, d2) =  (1 - \alpha) \cdot  lexSim(d1, d2) + \alpha \cdot semSim(d1, d2)$
and decide on an $\alpha$ by optimizing for a maximal
F-score on a development dataset.

In [ ]:
## Using Average scheme for semantic similarity measurements
def calculate_idiom_sim_avg(idiom1, idiom2, alpha=0.5):
  d1 = list(data.Definition)[list(data.Idiom).index(idiom1)]
  d2 = list(data.Definition)[list(data.Idiom).index(idiom2)]
  id_d1 = list(data.Idiom).index(idiom1)
  id_d2 = list(data.Idiom).index(idiom2)
  similarity_rate = (1 - alpha) * calculate_lex_sim(id_d1, id_d2) + \
                    alpha * calculate_sem_sim_avg(id_d1, id_d2)
  #print('Definition #1: {}\nDefinition #2: {}\nSimilarity rate:'.format(d1, d2, similarity_rate))
  return similarity_rate

#### Find idioms similar to a given idiom

In [ ]:
from tqdm import tqdm_notebook

In [ ]:
def find_similar_idioms(idiom1, idioms, method='average', top_k=5):
  similarities = {}
  for id, idiom in enumerate(tqdm_notebook(idioms)):
    #print('\n')
    if method.lower() == 'average':
      #print(idiom1, '<----->', idiom)
      similarities[id] = calculate_idiom_sim_avg(idiom1, idiom)
    elif method.lower() == 'weighted':
      similarities[id] = calculate_idiom_sim_weighted(idiom1, idiom)
    else:
      print('Incorrect method specified. Supported methods: average, weighted.\n'
      'Further calculations will use average method as default.')
      similarities[id] = calculate_idiom_sim_avg(idiom1, idiom)
    #print(similarities[id])
  print(similarities)
  sorted_dict = {}
  sorted_values = sorted(similarities.values())
  print(sorted_values)

  for i in tqdm_notebook(sorted_values):
    for k in similarities.keys():
      if similarities[k] == i:
        sorted_dict[k] = similarities[k]
        break
  print('Sorted Dict', sorted_dict)
  print('Idioms similar to "{}":\n'.format(idiom1))
  print('{} method used.'.format(method))
  sorted_list = list(sorted_dict.items())
  sorted_list.reverse()
  for i, id in enumerate(sorted_list[1 :top_k + 1]):
    print('Idiom #{}: {}\n\tIts definition: {}\n\tSimilarity rate: {}'.
          format(i + 1, idioms[id[0]], list(data.Definition)[id[0]], sorted_dict[id[0]]))  

### Examples

In [ ]:
find_similar_idioms('взять в голову', list(data.Idiom))


{0: 0.4468739071495019, 1: 0.4872368099472958, 2: 0.42478586281436637, 3: 0.4657830273624258, 4: 0.4657830273624258, 5: 0.46867987101629743, 6: 0.5019124903269649, 7: 0.4858917303546574, 8: 0.4858917303546574, 9: 0.44836484209470884, 10: 0.44836484209470884, 11: 0.4422495381174688, 12: 0.44401918885193115, 13: 0.4767420537182503, 14: 0.4550766384596717, 15: 0.4271983577143079, 16: 0.43547515456459207, 17: 0.4677352615076998, 18: 0.4517895220627729, 19: 0.48376060294182543, 20: 0.4939394443787162, 21: 0.4707395245460094, 22: 0.45260879056614745, 23: 0.4172999204181204, 24: 0.4391248327348447, 25: 0.48536334250342084, 26: 0.4270036298325858, 27: 0.418074372243726, 28: 0.47569051757789305, 29: 0.46720367353934944, 30: 0.4592970022213686, 31: 0.44835813677952413, 32: 0.4246772212626363, 33: 0.4706372867513912, 34: 0.5069389930343806, 35: 0.46617959276830434, 36: 0.45367841638442274, 37: 0.45367841638442274, 38: 0.45364544249339767, 39: 0.45364544249339767, 40: 0.4734012331027895, 41: 0.47


Sorted Dict {13586: 0.4029476345411447, 10483: 0.40841609027219217, 6321: 0.4090066792628858, 713: 0.4100473781293258, 9269: 0.4106937508746829, 12815: 0.4115643567603683, 6545: 0.4117796222665929, 6530: 0.4119709133379501, 3363: 0.4121724474328645, 2972: 0.412222629616891, 13475: 0.4123196037213563, 11271: 0.412354224540565, 4525: 0.4126337747823713, 10741: 0.4128358641574433, 5903: 0.41289816919682315, 257: 0.4130529109694056, 330: 0.4131231040947865, 13594: 0.4131241062269119, 1880: 0.41317689154548864, 317: 0.41344217853794163, 1380: 0.41377750650523715, 6265: 0.4137834111134756, 2569: 0.41381951188650756, 6477: 0.413823342518467, 12989: 0.4138953779412588, 11990: 0.41411274789778163, 5078: 0.4141486483704504, 10329: 0.41414945574222584, 1218: 0.4142190685506595, 1632: 0.4142380889998435, 9043: 0.414250082844705, 4865: 0.41428115532896365, 11378: 0.414300544719745, 1784: 0.4143249934689627, 12500: 0.41442066655271037, 8560: 0.4144228406316387, 6770: 0.41445643910025964, 9743: 0.41

In [ ]:
find_similar_idioms('слон на ухо наступил', list(data.Idiom))


{0: 0.34060464799404144, 1: 0.4019531309604645, 2: 0.37319372594356537, 3: 0.4470111131668091, 4: 0.44701407849788666, 5: 0.4396194964647293, 6: 0.3551327735185623, 7: 0.43144896626472473, 8: 0.4314510226249695, 9: 0.34267739951610565, 10: 0.34267762303352356, 11: 0.42197924852371216, 12: 0.4308643937110901, 13: 0.4125869572162628, 14: 0.39050692319869995, 15: 0.3755960762500763, 16: 0.41749607026576996, 17: 0.4297838807106018, 18: 0.4385870695114136, 19: 0.3574831783771515, 20: 0.4100741595029831, 21: 0.40904659032821655, 22: 0.40634165704250336, 23: nan, 24: 0.31869903206825256, 25: 0.39059843122959137, 26: 0.27368536591529846, 27: 0.2804690822958946, 28: 0.3973984569311142, 29: 0.37593674659729004, 30: 0.3669412434101105, 31: 0.5694425106048584, 32: 0.29358456283807755, 33: 0.4031040817499161, 34: 0.4412160813808441, 35: 0.42347031831741333, 36: 0.4360881894826889, 37: 0.4360901564359665, 38: 0.4312667101621628, 39: 0.4312686324119568, 40: 0.40372850000858307, 41: 0.403730183839798


Sorted Dict {26: 0.27368536591529846, 220: 0.2740534469485283, 227: 0.27491461485624313, 289: 0.27868954837322235, 59: 0.28035105019807816, 27: 0.2804690822958946, 68: 0.2824280187487602, 89: 0.2868525981903076, 106: 0.28940217941999435, 42: 0.29241807013750076, 32: 0.29358456283807755, 311: 0.29363611340522766, 97: 0.2975646182894707, 281: 0.29882190376520157, 247: 0.30434589833021164, 85: 0.3063216134905815, 86: 0.30717886984348297, 234: 0.3076382726430893, 279: 0.3098433315753937, 235: 0.3111612945795059, 299: 0.3120538741350174, 24: 0.31869903206825256, 81: 0.320682093501091, 316: 0.32072266936302185, 257: 0.325618177652359, 300: 0.33054591715335846, 70: 0.3324752449989319, 78: 0.3332453817129135, 223: 0.3339739739894867, 285: 0.33541229367256165, 278: 0.33916813135147095, 277: 0.3391685485839844, 103: 0.33983083069324493, 0: 0.34060464799404144, 9: 0.34267739951610565, 10: 0.34267762303352356, 92: 0.34624068439006805, 101: 0.346907302737236, 91: 0.3477092981338501, 72: 0.35217575

In [ ]:
find_similar_idioms('о двух головах', list(data.Idiom))


{0: 0.2567903697490692, 1: 0.35545405745506287, 2: 0.2839618995785713, 3: 0.33839187026023865, 4: 0.33839160203933716, 5: 0.37359268963336945, 6: 0.294237457215786, 7: 0.34410372376441956, 8: 0.34410327672958374, 9: 0.2573930248618126, 10: 0.25739144533872604, 11: 0.3453877866268158, 12: 0.3469708412885666, 13: 0.33285267651081085, 14: 0.31364141404628754, 15: 0.3531797081232071, 16: 0.32643459737300873, 17: 0.3433283120393753, 18: 0.3380591720342636, 19: 0.34742386639118195, 20: 0.37162594497203827, 21: 0.32221750915050507, 22: 0.3225455731153488, 23: nan, 24: 0.3712537884712219, 25: 0.33413033187389374, 26: 0.39369161427021027, 27: 0.3043353408575058, 28: 0.29602255672216415, 29: 0.2767203077673912, 30: 0.3251313865184784, 31: 0.32630592584609985, 32: 0.2949259579181671, 33: 0.3516206294298172, 34: 0.32246385514736176, 35: 0.339667484164238, 36: 0.34907378256320953, 37: 0.34907375276088715, 38: 0.34474942088127136, 39: 0.3447493314743042, 40: 0.34500207006931305, 41: 0.3450018316507


Sorted Dict {0: 0.2567903697490692, 10: 0.25739144533872604, 9: 0.2573930248618126, 29: 0.2767203077673912, 3540: 0.27702878415584564, 3539: 0.27702975273132324, 3970: 0.2772139087319374, 3542: 0.27744557708501816, 3541: 0.27744653075933456, 4110: 0.28013812005519867, 4109: 0.28013986349105835, 3579: 0.280797615647316, 3578: 0.2807989716529846, 3530: 0.2815031260251999, 3604: 0.2822134494781494, 4002: 0.28234703093767166, 4001: 0.2823486253619194, 4052: 0.2823946550488472, 4048: 0.2831450551748276, 4047: 0.28314588963985443, 3544: 0.2839546501636505, 2: 0.2839618995785713, 3598: 0.2845997139811516, 4080: 0.2852703630924225, 4095: 0.28530050814151764, 4094: 0.28530092537403107, 4225: 0.2868143692612648, 4224: 0.2868156060576439, 3975: 0.28693071752786636, 3998: 0.28696878999471664, 3997: 0.28697002679109573, 3960: 0.28700147569179535, 3971: 0.2871406301856041, 4155: 0.2885019853711128, 4154: 0.28850290924310684, 4195: 0.2900945469737053, 4194: 0.29009539633989334, 4193: 0.2908914387226

# Test

In [ ]:
data_test = data.sample(500, random_state=42)
data_test

Idiom  ...                                         Embeddings
11342  разводить тары-бары (растабары)  ...  [[0.031473745, 0.0100517105, 0.09077904, -0.00...
10145                   показать кукиш  ...  [[0.084294, -0.16787466, -0.09381893, 0.153512...
13580                  устоять в слове  ...  [[0.035985626, 0.02558849, 0.008714557, -0.029...
13289             точить балясы (лясы)  ...  [[0.016896844, 0.0076039596, 0.013299912, 0.00...
7802              не иметь духа (духу)  ...  [[0.120287456, 0.047326554, -0.08544881, 0.275...
...                                ...  ...                                                ...
10917                 прищемлять хвост  ...  [[0.048084106, -0.012743428, 0.00065506325, 0....
6674                 музейная редкость  ...  [[0.08264682, -0.058729313, -0.030634701, -0.0...
10239   положение хуже губернаторского  ...  [[-0.024919095, 0.03269283, 0.013005536, 0.010...
7938                   не помнить себя  ...  [[0.030255042, 0.18153343, -0.05075333, -0.144...
7023                       на посылках  ...  [[-0.11859715, 0.05384232, 0.015645575, 0.0641...

[500 rows x 3 columns]

In [ ]:
def find_similar_idioms_(idiom1, idioms, method='average', top_k=5):
  similarities = {}
  if method.lower() == 'average':
    print('Average method specified.')
    calculate_sim = calculate_idiom_sim_avg
  elif method.lower() == 'weighted':
    print('Weighted method specified.')
    calculate_sim = calculate_idiom_sim_weighted
  else:
    print('Incorrect method specified. Supported methods: average, weighted.\n'
    'Further calculations will use average method as default.')
    calculate_sim = calculate_idiom_sim_avg
  for id, idiom in enumerate(tqdm_notebook(idioms)):
    #print(id, idiom)
    if id < 13440:
      similarities[id] = calculate_sim(idiom1, idiom)
  sorted_dict = {}
  sorted_values = sorted(similarities.values())

  for i in sorted_values:
    for k in similarities.keys():
      if similarities[k] == i:
        sorted_dict[k] = similarities[k]
        break

  for i in tqdm_notebook(sorted_values):
    for k in similarities.keys():
      if similarities[k] == i:
        sorted_dict[k] = similarities[k]
        break
    
  sorted_list = list(sorted_dict.items())
  sorted_list.reverse()
  candidates = []
  for i, id in enumerate(sorted_list[1 :top_k + 1]):
    candidates.append([idioms[id[0]], list(data.Definition)[id[0]]])
    
  return candidates

In [ ]:
test_size = [i for i in range(601)]
test_ranges = test_size[::10]
test_ranges

[0,
 10,
 20,
 30,
 40,
 50,
 60,
 70,
 80,
 90,
 100,
 110,
 120,
 130,
 140,
 150,
 160,
 170,
 180,
 190,
 200,
 210,
 220,
 230,
 240,
 250,
 260,
 270,
 280,
 290,
 300,
 310,
 320,
 330,
 340,
 350,
 360,
 370,
 380,
 390,
 400,
 410,
 420,
 430,
 440,
 450,
 460,
 470,
 480,
 490,
 500,
 510,
 520,
 530,
 540,
 550,
 560,
 570,
 580,
 590,
 600]

In [ ]:
rows_all = []
for r in test_ranges:
  print(r, '/500_____________________\n')
  rows = []
  for i, idiom in enumerate(data_test.Idiom.values[r:r+10]):
    row = [[idiom, list(data.Definition)[list(data.Idiom).index(idiom)], ]]
    print(idiom, list(data.Definition)[list(data.Idiom).index(idiom)])
    candidates = find_similar_idioms_(idiom, list(data.Idiom))
    for candidate in candidates:
      row.append(candidate)
    rows.append(row)
  rows_all += rows

predictions = pd.DataFrame(rows_all)

0 /500_____________________

разводить тары-бары (растабары) Заниматься пустословием попусту болтать 
Average method specified.



показать кукиш То же что показывать дулю i кому А ты чай думал своей охотой я связалась с тобой бабья рожа Накося И показав ему кукиш стала стучать лбом о дверь снова воя и вскрикивая i М Горький Жизнь Матвея Кожемякина 
Average method specified.



устоять в слове Выполнить обещанное 
Average method specified.



точить балясы (лясы) Пустословить заниматься пустой болтовнёй Первонач вытачивать узорные фигурные столбики перил балясы от итал balaustro столбик точёные перильца лясы от польск lasa решётка чётка в строительном деле грохот c lightslategray c Максимов С Крылатые слова СПб 1899 С 35 
Average method specified.



не иметь духа (духу) Не отважиться не решиться что либо сказать сделать и т п 
Average method specified.


...


за один Вместе в согласии заодно 
Average method specified.



сукины (сучьи) дети p грубо прост p Бранное выражение передающее презрение резкое осуждение за что либо 
Average method specified.



сердце кровью заливается Кому либо невыносимо тяжело от душевной боли страха тревоги 
Average method specified.



сходя в гроб Перед смертью обычно достигнув преклонного возраста 
Average method specified.



наше вам с кисточкой Шутл Привет рад видеть 
Average method specified.


In [ ]:
predictions.to_csv('predictions_fastText100.csv', encoding='utf-8-sig')